# 感知机 Review

In [1]:
from IPython import display
video = lambda src: \
    display.Video("../media/videos/Perceptron/480p15/" + src, embed=True, width=400, height=300)

In [2]:
video("PreProc.mp4")

如图是一个巨大的坐标系，在这个坐标系中，我们有 5 个颜色不同的点。现在，你需要画一条直线来分开不同颜色的点。

作为人类，你应该很容易就能找到其中的一个解。比如这一条线，将 5 个点分成了 蓝色 和 黄色 两个部分。这个问题就叫做 分类 (Classification)，或者，更准确地说，你把点分成了两类，那就是 二分类 (Binary Classification)

那么如何表示每一个点呢？我们可以用坐标，或者说我们可以用 向量 (Vector) 来表示点的坐标。例如，第一个点我们记作向量 $\vec{x}^{(1)}$，左边的数代表第一个向量的第一个维度，这里是点的横坐标。右边的点代表第一个向量的第二各维度，这里是点的纵坐标。

你会发现，我们除了横纵坐标，还需要一个数据来描述点的颜色，于是我们用 标签 (Label) 来标记每个点的颜色，每个点的标签用 $y^{(i)}$ 表示。例如，第一个点的颜色是蓝色，我们就可以记作 $y^{(1)}=\text{BLUE}$，但是机器并不能阅读文字，于是我们会规定蓝色用 $1$ 代替，那第三个点是黄色，我们会规定黄色用 $-1$ 代替。

这样一来，我们每一个点都可以用一个包含三个元素的集合来表示，他们从左到右依次代表，第 $i$ 个点的第一个维度，也就是横坐标；第 $i$ 个点的第二个维度，也就是纵坐标；第 $i$ 个点的标签，也就是颜色。那平面中所有的点又会构成一个更大的集合，包含了我们训练模型用的所有点的数据。

In [3]:
video("ALine.mp4")

但是在正式开始之前，我们先来看一个有意思的问题：如何用直线划分点集。

如图是一个坐标轴和一个直线的一般式。我们可以给 $a_1, a_2, b$ 设定不同的初始值，然后就可以得到一条直线。改变 $b$ 的值，会让直线平移；改变 $a_1, a_2$ 的值会让直线旋转。我们在高中还学过法向量，这是一个与给定直线垂直的向量，它的终点就是 $a_1, a_2$ 构成的坐标。我们减少 $b$ 的值，并不会改变法向量的方向，而是让直线朝着“法向量正方向”指着的方向挪了一步。改变 $a_1, a_2$，直线的倾斜角开始变化，法向量也会跟着变化。

我们不妨将法向量记为 $\vec{w}$，于是可以写出另外一个式子： $0 = \vec{w} \cdot \vec{x} + b$，仔细观察，你会发现这个点乘的方程式其实和一般式是等价的。满足下面方程式的所有向量 $\vec{x}$ 的终点都会在这一条直线上。那如果不在直线上呢？

当我们试图将点朝着法向量指的大致方向移动时，表达式的值是正数。而当我们朝着法向量指的大致方向的反方向移动时，表达式的值是负数。因此，我们可以人为规定：表达式为正时，区域是蓝色的；表达式为负时，区域是黄色的。这样，我们就可以把原来表达式里的 $0$ 改为 $\hat{y}$，我们之前定义，$y$ 代表标签。在之前的例子中就是颜色。而 "hat" 代表预测值。我们于是就得到了一个，可以依据表达式的值来预测点的颜色的直线。

那么机器是如何找到这条直线的呢？其实远远没有想象的那么复杂。例如，假设这里有一个黄色点是我们需要学习的其中一个数据。很明显，根据标签他是黄色，也就是 $-1$，一个小于 $0$ 的数，而根据表达式带入坐标，他的标签预测值肯定是大于 $0$ 的。这代表我们的模型没有很好的分开这个黄色的点，于是模型就要学习这一个点并且修正自己。我们希望，这个点落在黄色区域，也就是让这条直线“旋转”一下就好，那机器的理解里，直线该按照什么方式旋转呢？

我们可以用一个向量来表示需要学习的点。由于法向量与直线始终垂直，所以旋转直线就是旋转法向量。也就是说，我们只要让法向量远离这个点的向量就好了。什么运算能够远离呢？**向量减法**！我们对两个向量做差，得到的新向量记作 $\vec{w}'$，于是，此时的向量就实现了旋转。但光旋转还不够，此时这个点还落在蓝色区域，我们还有一种办法，那就是平移。如之前看到的一样，我们减少 $b$ 的值，直线就会向上平移，此时的黄色区域就离黄色点更近了一步。

接下来，我们只需要让机器重复刚刚说过的步骤就好：向量做差，减少 $b$ 的值。这样，黄色区域就包裹了需要学习的点，而且蓝色区域也离这个点越来越远了。那如果这个点是蓝色的呢？我们只需要做向量加法，并且增加 $b$ 的值，就可以逼近它了。

于是我们可以总结出这样的学习方法：
- 如果预测与实际相同，不做动作
- 如果预测与实际不同，就要调整参数
    - 如果预测的值大于 0，而实际的值小于 0，例如现在，黄色的点被包裹在了蓝色区域内。说明法向量与这个点的向量太靠近了，于是我们可以通过
        - 向量减法，让法向量远离
        - 然后减少 $b$ 的值，我们就可以让蓝色区域离得更远。
    - 同样的，如果预测的值小于 0，而实际的值大于 0，例如现在，蓝色的点被包裹在了黄色区域内。说明法向量与这个点的向量太远了了，于是我们可以通过
        - 向量加法，让法向量靠近
        - 然后增加 $b$ 的值，让黄色区域离得更远

这就是感知机 (Perceptron) 的运作原理

In [4]:
video("LRate.mp4")

但是这样就行了吗？假设我们把各种参数作为自变量，学习效果作为因变量，把模型在学习的过程中调整参数看作调整自变量。假设有这样一条曲线代表了学习效果。如果我们每次以相同的幅度调整参数就很容易错过最佳的学习效果点。

因此，我们会设定一个学习率，你可以理解为“每次学习时，调整参数的幅度”，并且我们设定一个衰减函数，用来更新学习率，使其逐渐降低。在这里为了方便大家感受，我所设定的学习率就代表了图中的点每次移动的单位长度。

这样，我们在不断的学习中，学习率不断降低，摆动幅度越来越小，最后会让整个模型收敛在一个较佳的学习效果下。当学习率小到一定程度的时候，模型就会停止学习，并且给出当前学到的参数。

就像人类一样，学习到一定程度，学不动了就会停止。这样可以保证我们的模型不会一直循环，也不会再一些极端情况下死机或者反复横跳。

需要注意的是，学习率的初始值和衰减函数是我们人为设定的，不会被机器学习算法主动更新，却影响着学习的结果。类似这样的参数叫做超参数（hyperparameter）。以及，我们收敛的位置也不一定是，或者说，大概率不是完美的最优点。这部分的内容将会在后续进行更多探讨。

回顾刚才给出的学习函数，我们只需要在每次的更新数据前加上一个 $\eta$，也就是我们的学习率，我们的模型就能正确地停下来了。

值得一提的是，在实际的机器学习训练（可能不适用于感知机的训练）中，$\eta$ 的取值可能远比你之前想象的要小，$\eta=0.001, \eta=0.001$ 甚至 $0.0001, 0.0001$ 都是很有可能的。而衰减函数也有很多选择，最常见的就是一个常数乘以 $\eta$，这个常数也不会像我们刚才演示的那么小，通常是个很接近但小于 $1$ 的数，例如 $0.999$

In [5]:
video("Perc.mp4")

回到刚刚的坐标轴，不知道你有没有想过，机器最初的那一条直线到底是什么呢？实际上是随机的，毕竟机器可以一点点学到最优解。例如这一条直线，我们可以写成向量点乘的形式，那么 $-1, -1, 0$ 就是我们参数的随机初始值。上面我给出了一个叫做训练损失函数的东西，我们暂且理解为，在当前的这些点中有多少个分类错误了。具体的 Loss 函数我们在 SI 100+ 正课中有所提及。那机器就可以不断学习，改变参数，最终找到一条符合或者最接近要求的直线。当然，不一定只修改 $b$ 的值，修改 $\vec{w}$ 向量也是可以的。

但是在实际的训练中，我们不会贸然开始，而是会对这个数据做一些处理。就像这些点一直在右上角会让你感到不适，这样的值对机器的学习也会有所影响。我们可以分维度分别求出他们的平均值和标准差，然后带入这样一个公式。将每一个点的数据带入，我们就可以得到新的点的分布，是不是好看了很多？

这就是我们实际训练前对数据的一种预处理，叫做归一化。刚刚演示的就是归一化中常用的 Z-score 标准化，它可以使不同量纲的数据都可以比较，并且减少极端值的影响，适用于很多对距离敏感的算法。

In [6]:
video("Ntwk.mp4")

在讲完了感知机的算法原理、和数据的预处理之后，我们来看看感知机的模型，也就是神经网路为什么会被称为神经。

我们知道，生物学中一个神经元是由细胞体和突起组成。其中大而密的是树突，用来接受数据，长长的是轴突，用来传递数据。在神经网络中，我们会用一个圆和箭头来表示一个神经元。它也是我们神经网络中最小的组成单元。

其中圆形就像树突一样，可以接受别的神经元传来的数据，而箭头负责输出数据。

像图中一样，我们刚刚做出来的感知机就是这样一个模型，它分为两层，一层负责输入，有两个输入用的神经元可以接受两个输入，一层负责输出，只有一个神经元。在神经元的箭头上还有权重，其实就是我们之前看到的的法向量的各个维度，权重的绝对值越大，说明这个数据越“重要”。

于是我们就可以得到，输出层的神经元接受到的数据是 $w_1 x_1 + w_2 x_2$，在线性代数中，这叫做线性组合。例如，假设输入都是 1，其中一个权重为 0.7 ，另一个为 0.2，那么总输入就是 0.9。

但是你会发现，我们还少了一个参数，那就是之前说的 $b$，它代表偏置，有的地方也叫做阈值。顾名思义，这个阈值就像是一个阀门，我们不希望一个神经元很容易就兴奋，而是希望它超过某一定的数值才会兴奋，例如这一个神经元的偏置是 0.5 ，代表我们希望它超过 0.5 才兴奋。

那么这个偏置的值与两个权重，就共同构成了这一个感知机的三个参数。感知机学习的过程，就是不断根据输入数据比较输出，从而学习调整这三个参数的过程。由于输入层并不会对数据做任何函数的处理，我们通常忽略这一层，称这个感知机为单层感知机。

In [7]:
video("AcFun.mp4")

刚才我们说道，超过 0.5 才兴奋，于是自然而然的对输入减掉了 0.5，实际上我们是默认了，总输入的值大于等于 0 就相当于神经元被激活，小于 0 就相当于神经元没有被激活。

实际上，在神经网络的世界里，我们也有一个名为“激活函数”的函数，专门用来处理“谁代表了激活”的问题。例如，我们刚刚的想法就是，总输入大于等于 0 就是激活态，我们用类似二进制的 1 来表示，而小于 0 就是未激活态，我们用 0 来表示，那就会像是这样。像这样的函数叫做阶跃函数，顾名思义就像是一个阶梯，是不连续也不平滑的。所有的激活函数都能够将不论大小的总输入全部映射到 0 到 1，用来确定这个神经元的输出，代表了这个神经元到底是否已经激活。

但是阶跃函数有一个致命的缺点：不连续和不平滑。这就会导致，如果总输入刚好从 -0.0001 变为 0，这个神经元的输出就会猛然跳到 1，造成像蝴蝶效应一样的连锁而可怕的后果，因此我们会用另一个 Sigmoid 函数代替，它大概长这样，在越小于 0 的地方越趋近于 0，越大于 0 的地方越趋近于 1。并且还是平滑的，这就很好的解决了我们之前提到的问题。

其实 Sigmoid 函数也不是完美的，毕竟如果输入数据太大，他的输出就会变化的非常微小，所以现在更流行的是 ReLU 函数，它大概长这样，也就是，小于 0 就是 0，大于 0 就输出本身。你可能会疑惑，不是只有 0 到 1 才有意义吗？实际上，这也是一种思维上的局限，我们何必按照生物规律来模拟神经元呢？我们就算得到 0 与 1 之外的结果，只要稍加比较或者设定一个限度，也可以有所意义。

In [8]:
video("XOR.mp4")

回到感知机，我们来看一个具体的问题，这是有名的 XOR 问题。所谓 XOR 运算也就是 两个输入不同就输出 1。例如图中，所有横坐标与纵坐标相等的点都是黄色，标签为 -1；而所有横纵坐标不同的点都是蓝色，标签为 1。很显然，这个图中的四个点是没办法用一条直线区分开两种颜色的。这种问题被称作“线性不可分”，也就是说，一条三个参数的直线，也就是我们刚才的那种三个参数的单层感知机是无法做到区分的。这时候就要引入多层感知机了。

In [9]:
video("MLP.mp4")

例如，这就是一个能够解决刚刚的问题的感知机，相比之下，我们只添加了一层，两个神经元，添加的这一层被称为 隐藏层。我们假定，蓝色的箭头代表权重为 1 ，黄色的箭头代表权重为 -1，并且隐藏层和输出层的偏置都为 0.5，我们随意抽取一个数据来看。例如当输入分别为 1 和 0 的时候，由于输入不同，因此我们知道结果应该为 1。让我们手动算一算。

首先，这两个数据会被输入层捕获，并且激活一个神经元。接下来，对于隐藏层上面的神经元，它会接受两个输入。其中一个输入 1 乘以蓝色的权重 1 得到 1，另一个 0 乘以黄色的权重得到 0，相加就得到 1 这个总输入，别忘了减去偏置 0.5，得到了 1 - 0.5 = 0.5，再根据激活函数，0.5 对应的是一个趋近于 1 的值，我们忽略误差，不妨认为输出的值就是 1，也就是这个神经元被激活了。下面的神经元也是一样，加权相加后得到的是 -1，减去偏置得到 -1.5，对应激活函数中趋近 0 的一个值，我们忽略小量，不妨认为输出就是 0，也就是这个神经元没有被激活。最后汇总到输出层的总输入是 1，减去偏置得到 0.5，如法炮制以下也就是相当于输出是被激活的状态。我们就成功验证了其中一个情况。

实际上，四个情况都能够满足，而我们只添加了少少的一层隐含层，是不是非常神奇。

In [10]:
video("DumyNd.mp4")